# Test synthetic trajectories generation

In [55]:
import xarray as xr
import pandas as pd
import numpy as np

import hvplot.xarray
import hvplot.pandas
import holoviews as hv

import matplotlib.pyplot as plt
from cycler import cycler

from sstats import signals as sg
from sstats import sigp as sigp
from sstats import tseries as ts
from sstats import get_cmap_colors

import pynsitu as pyn
from pynsitu.geo import spectral_diff
#import lib as lib
import synthetic_traj as st
from synthetic_traj import pos_vel_acc_spectral

---

## generate synthetic timeseries

We sum a low frequency signal, a (polarized) near-inertial component and (non-polarized) semi-diurnal and diurnal tidal signals


In [78]:
# timeline: 100 days with hourly sampling
dt = 1/24
t = (50, 1/24/60) # use it instead of (50, 1/24/60 because otherwise not regularly sampled
# number of random draws
N = 10 

# use a common decorrelation timescale, no rationale
#T = [5,10,20,40]
T = 10

# velocity amplitudes
U_low = 0.3
U_ni = 0.2
U_2 = 0.05
U_1 = 0.02

tau_eta = 0.1 # short timescale
n_layers = 5 # number of layers

In [91]:
def dataset2dataframe(ds):
    DF = []
    for d in ds.draw:
        df = ds.sel(draw=d).to_dataframe()
        DF.append(df)
    return pd.concat(DF)

def pos_vel_acc_spectral(df, dt, suf='') :
    #compute position
    df["x"+suf] = df.groupby('draw')['u'+suf].apply(pyn.geo.spectral_diff, dt, order = -1)
    df["y"+suf] = df.groupby('draw')['v'+suf].apply(pyn.geo.spectral_diff, dt, order = -1)
    #update velocities (diff cumulate_integrate vs differentiate do not give same result, numerical errors)
    df["u"+suf] = df.groupby('draw')['x'+suf].apply(pyn.geo.spectral_diff, dt, order = 1)
    df["v"+suf] = df.groupby('draw')['y'+suf].apply(pyn.geo.spectral_diff, dt, order = 1)
    df["U"+suf] = np.sqrt(df["u"+suf]**2+df["v"+suf]**2)
    # compute acceleration
    df["ax"+suf] = df.groupby('draw')['x'+suf].apply(pyn.geo.spectral_diff, dt, order =2)
    df["ay"+suf] = df.groupby('draw')['y'+suf].apply(pyn.geo.spectral_diff, dt, order =2)
    df["Axy"+suf] = np.sqrt(df["ax"+suf]**2+df["ay"+suf]**2)
        
def synthetic_traj(
    t, N, T, tau_eta, n_layers, U_low, U_ni, U_2, U_1, out_put='dataset', all_comp_pos_acc =False, spectral_diff=True
):
    """
    Generate a synthetic trajectory
    Parameters:
    -----------
            t : tuple, ndarray or int or str
                Time series
            N : int,
                nb of draws
            T : float 
                long correleration time scale in days
            tau_eta : float,
                short correlation scale in days
            n_layers : int
                number of layers for OU process
            U_low : float, 
                background std m/s
            U_ni : float
                amplitude of the inertial term m/s
            U_2 : float, 
                amplitude of semi-diurnal tide component m/s
            U_1 : float, 
                amplitude of diurnal tide component m/s 
            out_put : str,
            all_comp_pos_acc : boolean
    """
    list_uv = []
    list_u = []
    list_v = []
    
    t0 = pd.Timestamp("2000/01/01")
    type_t = isinstance(t[1], str)
    if type_t:
        t_date = pd.date_range(t0, t0 + t[0]* pd.Timedelta("1D"), freq=t[1])
        t = (t_date -t0)/pd.Timedelta("1D")
    
    if U_low != None:
        ## low frequency signal: a la Viggiano
        u_low = (
            ts.spectral_viggiano(t, T, tau_eta, n_layers, draws=N, seed=0)
            .compute()
            .rename("u_low")
            * U_low
        )
        v_low = (
            ts.spectral_viggiano(t, T, tau_eta, n_layers, draws=N, seed=1)
            .compute()
            .rename("v_low")
            * U_low
        )
        list_uv += [u_low, v_low]
        list_u.append("u_low")
        list_v.append("v_low")

    if U_ni != None:
        ## near-inertial signal: Sykulski et al. 2016

        f = pyn.geo.coriolis(45) * 86400
        E_ni = lambda omega: 1 / ((omega + f) ** 2 + T**-2)  ##CHANGE + to -

        uv_ni = ts.spectral(t, spectrum=E_ni, draws=N).compute() * U_ni
        u_ni = np.real(uv_ni).rename("u_ni")
        v_ni = np.imag(uv_ni).rename("v_ni")
        list_uv += [u_ni, v_ni]
        list_u.append("u_ni")
        list_v.append("v_ni")

    ## tidal signals

    # see high frequency spectrum
    # u_high = sg.high_frequency_signal()
    # u_high.analytical_spectrum

    # semi-diurnal
    if U_2 != None:
        omega0 = 2 * np.pi * 2  # semi-diurnal
        E_2 = lambda omega: (omega**2 + omega0**2 + T**-2) / (
            (omega**2 - omega0**2) ** 2
            + T**-2 * (omega**2 + omega0**2)
            + T**-4
        )

        uv_2 = ts.spectral(t, spectrum=E_2, draws=N).compute() * U_2
        u_2 = np.real(uv_2).rename("u_2")
        v_2 = np.imag(uv_2).rename("v_2")
        list_uv += [u_2, v_2]
        list_u.append("u_2")
        list_v.append("v_2")

    # diurnal
    if U_1 != None:
        omega0 = 2 * np.pi  # semi-diurnal
        E_1 = lambda omega: (omega**2 + omega0**2 + T**-2) / (
            (omega**2 - omega0**2) ** 2
            + T**-2 * (omega**2 + omega0**2)
            + T**-4
        )

        uv_1 = ts.spectral(t, spectrum=E_1, draws=N).compute() * U_1
        u_1 = np.real(uv_1).rename("u_1")
        v_1 = np.imag(uv_1).rename("v_1")
        list_uv += [u_1, v_1]
        list_u.append("u_1")
        list_v.append("v_1")

    # combine all time series
    ds = xr.merge(list_uv)
    ds["uo"] = sum([ds[u] for u in list_u]).assign_attrs(units="m/s")
    ds["vo"] = sum([ds[v] for v in list_v]).assign_attrs(units="m/s")
    
    # transform time in actual dates
    if not type_t :
        t_date = t0 + ds['time'] * pd.Timedelta("1D")
    ds["time_days"] = ds["time"].assign_attrs(units="days")
    ds["time"] = t_date
    
    if not spectral_diff :
        ds["x"] = ds["uo"].cumulative_integrate("time", datetime_unit='s').assign_attrs(units="m")
        ds["y"] = ds["vo"].cumulative_integrate("time", datetime_unit='s').assign_attrs(units="m")
        ds['X'] = ds['x']**2 + ds['y']**2
        if all_comp_pos_acc :
            def pos(ds, suf=''):
                ds["x"+suf] = ds["u"+suf].cumulative_integrate("time", datetime_unit = 's').assign_attrs(units="m")
                ds["y"+suf] = ds["v"+suf].cumulative_integrate("time", datetime_unit = 's').assign_attrs(units="m")
            pos(ds, suf ='_low')
            pos(ds, suf ='_ni')
            pos(ds, suf ='_1')
            pos(ds, suf='_2')

    # compute xy, uv and axy in fourier space
    # dataframe
    df = dataset2dataframe(ds)
    dt = (df.index[1] - df.index[0])/pd.Timedelta('1s')
    
    if spectral_diff:
        #xy
        df['x'] = df.groupby('draw')['uo'].apply(pyn.geo.spectral_diff , dt, order = -1)
        df['y'] = df.groupby('draw')['vo'].apply(pyn.geo.spectral_diff, dt, order = -1)
        df['X'] = np.sqrt(df['x']**2+df['y']**2)
        #uv
        df['u'] = df.groupby('draw')['x'].apply(pyn.geo.spectral_diff, dt, order = 1)
        df['v'] = df.groupby('draw')['y'].apply(pyn.geo.spectral_diff, dt, order = 1)
        df['U'] = np.sqrt(df['u']**2+df['v']**2)
        #axay
        df['ax'] = df.groupby('draw')['x'].apply(pyn.geo.spectral_diff, dt, order = 2)
        df['ay'] = df.groupby('draw')['y'].apply(pyn.geo.spectral_diff, dt, order = 2)
        df['Axy'] = np.sqrt(df['ax']**2+df['ay']**2)
        
        if all_comp_pos_acc:
            pos_vel_acc_spectral(df, dt, suf = '_low')
            pos_vel_acc_spectral(df, dt, suf = '_ni')
            pos_vel_acc_spectral(df, dt, suf = '_2')
            pos_vel_acc_spectral(df, dt, suf = '_1')
    else : 
        #uv
        df = df.groupby('draw').apply(pyn.geo.compute_velocities,time='index', distance='xy', names=('u', 'v', 'U'), fill_startend=True, centered=True)
        #axay
        df = df.groupby('draw').apply(pyn.geo.compute_accelerations,from_ =('xy', 'x', 'y'), names=('ax', 'ay', 'Axy'))

    df = df.groupby('draw').apply(pyn.geo.compute_dt, time='index')
    print(df.x.mean())
    if out_put == 'dataset' : 
        df = df.reset_index().set_index(['time', 'draw'])
        ds = df.to_xarray()
        return ds
    else : 
        return df
    return ds

In [92]:
t

(50, 0.0006944444444444444)

In [93]:
ds = synthetic_traj(t, N , T, U_low, U_ni, U_2, U_1, tau_eta, n_layers)
ds

16077.22704178676


<xarray.Dataset>
Dimensions:    (time: 72001, draw: 10)
Coordinates:
  * time       (time) datetime64[ns] 2000-01-01 ... 2000-02-19T23:59:59.99999...
  * draw       (draw) int64 0 1 2 3 4 5 6 7 8 9
Data variables: (12/21)
    u_low      (time, draw) float64 -0.03989 0.003581 ... 0.006042 -0.0468
    v_low      (time, draw) float64 -0.04525 0.03854 ... 0.04083 0.09929
    u_ni       (time, draw) float64 0.001457 -0.01758 ... 0.003801 -0.008212
    v_ni       (time, draw) float64 0.01695 0.005731 ... -0.008042 -0.01273
    u_2        (time, draw) float64 -0.05701 -0.05893 ... 0.03521 -0.04532
    v_2        (time, draw) float64 -0.1121 0.1348 -0.0489 ... 0.02284 0.0381
    ...         ...
    v          (time, draw) float64 0.0001254 -0.0001501 ... -0.0002082
    U          (time, draw) float64 0.0002429 0.0001816 ... 0.0002074 0.0002091
    ax         (time, draw) float64 -0.1779 0.1116 -0.1423 ... -0.1441 0.2223
    ay         (time, draw) float64 -0.1262 -0.03118 -0.0157 ... 0.1698 0.09308
    Axy        (time, draw) float64 0.2181 0.1159 0.1432 ... 0.1797 0.2227 0.241
    dt         (time, draw) float64 60.0 60.0 60.0 60.0 ... 60.0 60.0 60.0 60.0

In [101]:
ds = synthetic_traj((50, '1min'), N , T, U_low, U_ni, U_2, U_1, tau_eta, n_layers, spectral_diff=True)
ds

16077.227042054667


<xarray.Dataset>
Dimensions:    (time: 72001, draw: 10)
Coordinates:
  * time       (time) datetime64[ns] 2000-01-01 ... 2000-02-20
  * draw       (draw) int64 0 1 2 3 4 5 6 7 8 9
Data variables: (12/21)
    u_low      (time, draw) float64 -0.03989 0.003581 ... 0.006042 -0.0468
    v_low      (time, draw) float64 -0.04525 0.03854 ... 0.04083 0.09929
    u_ni       (time, draw) float64 0.001457 -0.01758 ... 0.003801 -0.008212
    v_ni       (time, draw) float64 0.01695 0.005731 ... -0.008042 -0.01273
    u_2        (time, draw) float64 -0.05701 -0.05893 ... 0.03521 -0.04532
    v_2        (time, draw) float64 -0.1121 0.1348 -0.0489 ... 0.02284 0.0381
    ...         ...
    v          (time, draw) float64 0.0001254 -0.0001501 ... -0.0002082
    U          (time, draw) float64 0.0002429 0.0001816 ... 0.0002074 0.0002091
    ax         (time, draw) float64 -0.1779 0.1116 -0.1423 ... -0.1441 0.2223
    ay         (time, draw) float64 -0.1262 -0.03118 -0.0157 ... 0.1698 0.09308
    Axy        (time, draw) float64 0.2181 0.1159 0.1432 ... 0.1797 0.2227 0.241
    dt         (time, draw) float64 60.0 60.0 60.0 60.0 ... 60.0 60.0 60.0 60.0

In [102]:
dscd = synthetic_traj((50, '1min'), N , T, U_low, U_ni, U_2, U_1, tau_eta, n_layers, spectral_diff=False)
dscd

16077.225663766867


<xarray.Dataset>
Dimensions:    (time: 72001, draw: 10)
Coordinates:
  * time       (time) datetime64[ns] 2000-01-01 ... 2000-02-20
  * draw       (draw) int64 0 1 2 3 4 5 6 7 8 9
Data variables: (12/21)
    u_low      (time, draw) float64 -0.03989 0.003581 ... 0.006042 -0.0468
    v_low      (time, draw) float64 -0.04525 0.03854 ... 0.04083 0.09929
    u_ni       (time, draw) float64 0.001457 -0.01758 ... 0.003801 -0.008212
    v_ni       (time, draw) float64 0.01695 0.005731 ... -0.008042 -0.01273
    u_2        (time, draw) float64 -0.05701 -0.05893 ... 0.03521 -0.04532
    v_2        (time, draw) float64 -0.1121 0.1348 -0.0489 ... 0.02284 0.0381
    ...         ...
    v          (time, draw) float64 -2.759 -0.6564 -0.328 ... -3.701 -2.067
    U          (time, draw) float64 4.724 2.503 3.13 2.787 ... 3.858 4.851 5.274
    ax         (time, draw) float64 -0.000528 0.0002292 ... -8.99e-06 0.000239
    ay         (time, draw) float64 0.0002486 -0.0003416 ... 0.0003735 0.001499
    Axy        (time, draw) float64 0.0005836 0.0004114 ... 0.0003736 0.001518
    dt         (time, draw) float64 60.0 60.0 60.0 60.0 ... 60.0 60.0 60.0 60.0

In [103]:
d=0
hvplot=(ds.isel(draw=d).x.hvplot(label='spectral') * dscd.isel(draw=d).x.hvplot(label='cd')
 +ds.isel(draw=d).u.hvplot(label='spectral') * dscd.isel(draw=d).u.hvplot(label='cd')
 +ds.isel(draw=d).ax.hvplot(label='spectral') * dscd.isel(draw=d).ax.hvplot(label='cd'))
layout = hv.Layout(hvplot).cols(1)

layout

:Layout
   .Overlay.I   :Overlay
      .Curve.Spectral :Curve   [time]   (x)
      .Curve.Cd       :Curve   [time]   (x)
   .Overlay.II  :Overlay
      .Curve.Spectral :Curve   [time]   (u)
      .Curve.Cd       :Curve   [time]   (u)
   .Overlay.III :Overlay
      .Curve.Spectral :Curve   [time]   (ax)
      .Curve.Cd       :Curve   [time]   (ax)